In [160]:
#En este cuadernos se hará el trabajo principal del proyecto final

In [161]:
import pandas as pd
import numpy as np
print("¡Hola, Proyecto Final del Curso!")

¡Hola, Proyecto Final del Curso!


# INTRODUCCIÓN - PLANTEAMIENTO DEL PROBLEMA

## Problema

Se pretende responder la siguiente pregunta: ¿en qué zona de Toronto es mejor colocar un gimnasio?

## Público objetivo

Un emprendedor tiene el capital para colocar un gimnasio en cualquier parte de Toronto, por ello me contrata para determinar la mejor ubicación de éste, en aras de cubrir la demanda insatisfecha en la zona.

## Criterio de colocación

El gimnasio deberá ser colocado en la zona donde menos gimnasios hallan.

## Metodología

1. Con los datos de Foursquare de Toronto se hallaran los locales que hay en cada zona marcada por el código postal.
2. Se verificarán cuántos gimnasios hay en cada zona y se creará una tabla con todos ellos.
3. Se marcarán esos gimnasios en el mapa.
4. Se creará un radio de influencia de cada gimnasio correspondiente a una medida de radio de gran amplitud.
5. Se mirará en que zona hay menos influencia de gimnasios.

## Datos usados

Los datos que se usarán son netamente los brindados por Foursquare, por cuanto tiene todo el repositorio de locales con 
su ubicación que permiten determinar la conveniencia geográfica de la puesta en marcha de un gimnasio en determinada zona.

# ELABORACIÓN

In [162]:
# EXTRAER DATOS
#Usé Excel para traerlos y depurarlos, luego los puse como lista aquí y al final los cargo directamente como lista.
import pandas as pd
import numpy as np # librería para manejar datos vectorizados

import pandas as pd # librería para análisis de datos
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # librería para manejar archivos JSON 

#!conda install -c conda-forge geopy --yes # retirar el comentario de esta línea si no ha completado el laboratorio de la API de FourSquare 
from geopy.geocoders import Nominatim # convertir una dirección en valores de latitud y longitud

import requests # librería para manejar solicitudes
from pandas.io.json import json_normalize # librería para convertir un archivo json en un dataframe pandas

# Matplotlib y módulos asociados para graficar
import matplotlib.cm as cm
import matplotlib.colors as colors

# importar k-means desde la fase de agrupación
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes # retirar el comentario de esta línea si no ha completado el laboratorio de la API de FourSquare
import folium # librería para graficar mapas 

print('Libraries imported.')


lista1=['M3A', 'M4A', 'M5A', 	'M6A', 	'M7A', 	'M9A', 	'M1B', 	'M3B', 	'M4B', 	'M5B', 	'M6B', 	'M9B', 	'M1C', 	'M3C', 	'M4C', 	'M5C', 	'M6C', 	'M9C', 	'M1E', 	'M4E', 	'M5E', 	'M6E', 	'M1G', 	'M4G', 	'M5G', 	'M6G', 	'M1H', 	'M2H', 	'M3H', 	'M4H', 	'M5H', 	'M6H', 	'M1J', 	'M2J', 	'M3J', 	'M4J', 	'M5J', 	'M6J', 	'M1K', 	'M2K', 	'M3K', 	'M4K', 	'M5K', 	'M6K', 	'M1L', 	'M2L', 	'M3L', 	'M4L', 	'M5L', 	'M6L', 	'M9L', 	'M1M', 	'M2M', 	'M3M', 	'M4M', 	'M5M', 	'M6M', 	'M9M', 	'M1N', 	'M2N', 	'M3N', 	'M4N', 	'M5N', 	'M6N', 	'M9N', 	'M1P', 	'M2P', 	'M4P', 	'M5P', 	'M6P', 	'M9P', 	'M1R', 	'M2R', 	'M4R', 	'M5R', 	'M6R', 	'M7R', 	'M9R', 	'M1S', 	'M4S', 	'M5S', 	'M6S', 	'M1T', 	'M4T', 	'M5T', 	'M1V', 	'M4V', 	'M5V', 	'M8V', 	'M9V', 	'M1W', 	'M4W', 	'M5W', 	'M8W', 	'M9W', 	'M1X', 	'M4X', 	'M5X', 	'M8X', 	'M4Y', 	'M7Y', 	'M8Y', 	'M8Z'] 
lista2=['North York','North York',	'Downtown Toronto',	'North York',	"Queen's Park",	'Etobicoke',	'Scarborough',	'North York',	'East York',	'Downtown Toronto',	'North York',	'Etobicoke',	'Scarborough',	'North York',	'East York',	'Downtown Toronto',	'York',	'Etobicoke',	'Scarborough',	'East Toronto',	'Downtown Toronto',	'York',	'Scarborough',	'East York',	'Downtown Toronto',	'Downtown Toronto',	'Scarborough',	'North York',	'North York',	'East York',	'Downtown Toronto',	'West Toronto',	'Scarborough',	'North York',	'North York',	'East York',	'Downtown Toronto',	'West Toronto',	'Scarborough',	'North York',	'North York',	'East Toronto',	'Downtown Toronto',	'West Toronto',	'Scarborough',	'North York',	'North York',	'East Toronto',	'Downtown Toronto',	'North York',	'North York',	'Scarborough',	'North York',	'North York',	'East Toronto',	'North York',	'York',	'North York',	'Scarborough',	'North York',	'North York',	'Central Toronto',	'Central Toronto',	'York',	'York',	'Scarborough',	'North York',	'Central Toronto',	'Central Toronto',	'West Toronto',	'Etobicoke',	'Scarborough',	'North York',	'Central Toronto',	'Central Toronto',	'West Toronto',	'Mississauga',	'Etobicoke',	'Scarborough',	'Central Toronto',	'Downtown Toronto',	'West Toronto',	'Scarborough',	'Central Toronto',	'Downtown Toronto',	'Scarborough',	'Central Toronto',	'Downtown Toronto',	'Etobicoke',	'Etobicoke',	'Scarborough',	'Downtown Toronto',	'Downtown Toronto',	'Etobicoke',	'Etobicoke',	'Scarborough',	'Downtown Toronto',	'Downtown Toronto',	'Etobicoke',	'Downtown Toronto',	'East Toronto',	'Etobicoke',	'Etobicoke']
lista3=['Parkwoods', 'Victoria Village', 'Regent Park, Harbourfront', 'Lawrence Manor, Lawrence Heights', 'Ontario Provincial Government', 'Islington Avenue', 'Malvern, Rouge', 'Don Mills', 'Parkview Hill, Woodbine Gardens', 'Garden District,\xa0Ryerson', 'Glencairn', 'West Deane Park, Princess Gardens, Martin Grove, Islington, Cloverdale', 'Rouge Hill, Port Union, Highland Creek', 'Don Mills, Flemingdon Park', 'Woodbine Heights', 'St. James Town', 'Humewood-Cedarvale', 'Eringate, Bloordale Gardens, Old Burnhamthorpe, Markland Wood', 'Guildwood, Morningside, West Hill', 'The Beaches', 'Berczy Park', 'Caledonia-Fairbanks', 'Woburn', 'Leaside', 'Central\xa0Bay Street', 'Christie', 'Cedarbrae', 'Hillcrest Village', 'Bathurst Manor, Wilson Heights, Downsview\xa0North', 'Thorncliffe Park', 'Richmond, Adelaide, King', 'Dufferin, Dovercourt Village', 'Scarborough Village', 'Fairview, Henry Farm, Oriole', 'Northwood Park, York University', 'The Danforth', 'Harbourfront\xa0East, Union Station, Toronto Islands', 'Little Portugal, Trinity', 'Kennedy Park, Ionview, East\xa0Birchmount Park', 'Bayview Village', 'Downsview, CFB Toronto', 'The Danforth\xa0West, Riverdale', 'Toronto Dominion Centre, Design Exchange', 'Brockton, Parkdale Village, Exhibition Place', 'Golden Mile, Clairlea, Oakridge', 'York Mills, Silver Hills', 'Downsview', 'India Bazaar, The Beaches\xa0West', 'Commerce Court, Victoria Hotel', 'North Park, Maple Leaf Park, Upwood Park', 'Humber Summit', 'Cliffside, Cliffcrest, Scarborough Village\xa0West', 'Willowdale, Newtonbrook', 'Downsview', 'Studio District', 'Bedford Park, Lawrence Manor\xa0East', 'Del Ray,\xa0Mount Dennis, Keelsdale and Silverthorn', 'Humberlea, Emery', 'Birch Cliff, Cliffside\xa0West', 'Willowdale', 'Downsview', 'Lawrence Park', 'Roselawn', 'Runnymede, The Junction\xa0North', 'Weston', 'Dorset Park, Wexford Heights, Scarborough Town Centre', 'York Mills\xa0West', 'Davisville\xa0North', 'Forest Hill\xa0North & West', 'High Park, The Junction\xa0South', 'Westmount', 'Wexford, Maryvale', 'Willowdale', 'North Toronto\xa0West', 'The Annex, North Midtown, Yorkville', 'Parkdale, Roncesvalles', 'Canada Post Gateway Processing Centre', 'Kingsview Village, St. Phillips, Martin Grove Gardens, Richview Gardens', 'Agincourt', 'Davisville', 'University of Toronto, Harbord', 'Runnymede, Swansea', "Clarks Corners,\xa0Tam O'Shanter, Sullivan", 'Moore Park, Summerhill\xa0East', 'Kensington Market, Chinatown, Grange Park', "Milliken, Agincourt North, Steeles\xa0East,\xa0L'Amoreaux\xa0East", 'Summerhill\xa0West,\xa0Rathnelly, South Hill, Forest Hill\xa0SE,\xa0Deer Park', 'CN Tower, King and Spadina, Railway Lands, Harbourfront\xa0West, Bathurst Quay,\xa0South Niagara, Island airport', 'New Toronto, Mimico\xa0South, Humber Bay Shores', 'South Steeles, Silverstone, Humbergate,\xa0Jamestown, Mount Olive, Beaumond Heights, Thistletown, Albion Gardens', "Steeles\xa0West,\xa0L'Amoreaux\xa0West", 'Rosedale', 'Stn A PO Boxes', 'Alderwood, Long Branch', 'Clairville, Humberwood, Woodbine Downs, West Humber, Kipling Heights,\xa0Rexdale, Elms, Tandridge, Old Rexdale', 'Upper Rouge', 'St. James Town, Cabbagetown', 'First Canadian Place, Underground city', 'The Kingsway, Montgomery Road,\xa0Old Mill\xa0North', 'Church and Wellesley', 'Business reply mail\xa0Processing Centre', "Old Mill\xa0South, King's Mill Park,\xa0Sunnylea,\xa0Humber Bay, Mimico\xa0NE,\xa0The Queensway\xa0East, Royal York South East, Kingsway Park South East", 'Mimico\xa0NW,\xa0The Queensway\xa0West, South of Bloor, Kingsway Park South West, Royal York South West']
user_list = list(zip(lista1,lista2,lista3))
df=pd.DataFrame(user_list, columns=["PostalCode","Borough","Neighborhood"])
df=df.set_index("PostalCode")
df.sort_values(by=["PostalCode"])

Libraries imported.


Borough  \
PostalCode                     
M1B              Scarborough   
M1C              Scarborough   
M1E              Scarborough   
M1G              Scarborough   
M1H              Scarborough   
M1J              Scarborough   
M1K              Scarborough   
M1L              Scarborough   
M1M              Scarborough   
M1N              Scarborough   
M1P              Scarborough   
M1R              Scarborough   
M1S              Scarborough   
M1T              Scarborough   
M1V              Scarborough   
M1W              Scarborough   
M1X              Scarborough   
M2H               North York   
M2J               North York   
M2K               North York   
M2L               North York   
M2M               North York   
M2N               North York   
M2P               North York   
M2R               North York   
M3A               North York   
M3B               North York   
M3C               North York   
M3H               North York   
M3J               North York   
M3K               North York   
M3L               North York   
M3M               North York   
M3N               North York   
M4A               North York   
M4B                East York   
M4C                East York   
M4E             East Toronto   
M4G                East York   
M4H                East York   
M4J                East York   
M4K             East Toronto   
M4L             East Toronto   
M4M             East Toronto   
M4N          Central Toronto   
M4P          Central Toronto   
M4R          Central Toronto   
M4S          Central Toronto   
M4T          Central Toronto   
M4V          Central Toronto   
M4W         Downtown Toronto   
M4X         Downtown Toronto   
M4Y         Downtown Toronto   
M5A         Downtown Toronto   
M5B         Downtown Toronto   
M5C         Downtown Toronto   
M5E         Downtown Toronto   
M5G         Downtown Toronto   
M5H         Downtown Toronto   
M5J         Downtown Toronto   
M5K         Downtown Toronto   
M5L         Downtown Toronto   
M5M               North York   
M5N          Central Toronto   
M5P          Central Toronto   
M5R          Central Toronto   
M5S         Downtown Toronto   
M5T         Downtown Toronto   
M5V         Downtown Toronto   
M5W         Downtown Toronto   
M5X         Downtown Toronto   
M6A               North York   
M6B               North York   
M6C                     York   
M6E                     York   
M6G         Downtown Toronto   
M6H             West Toronto   
M6J             West Toronto   
M6K             West Toronto   
M6L               North York   
M6M                     York   
M6N                     York   
M6P             West Toronto   
M6R             West Toronto   
M6S             West Toronto   
M7A             Queen's Park   
M7R              Mississauga   
M7Y             East Toronto   
M8V                Etobicoke   
M8W                Etobicoke   
M8X                Etobicoke   
M8Y                Etobicoke   
M8Z                Etobicoke   
M9A                Etobicoke   
M9B                Etobicoke   
M9C                Etobicoke   
M9L               North York   
M9M               North York   
M9N                     York   
M9P                Etobicoke   
M9R                Etobicoke   
M9V                Etobicoke   
M9W                Etobicoke   

                                                 Neighborhood  
PostalCode                                                     
M1B                                            Malvern, Rouge  
M1C                    Rouge Hill, Port Union, Highland Creek  
M1E                         Guildwood, Morningside, West Hill  
M1G                                                    Woburn  
M1H                                                 Cedarbrae  
M1J                                       Scarborough Village  
M1K               Kennedy Park, Ionview, East Birchmount Park  
M1L                           Golden Mile, Clairlea, Oakridge  
M1M           Cliffs

In [163]:
#Cargo el archivo de coordenadas y ordeno por PostalCode
coordenadas=pd.read_csv("D:\Descargas\Geospatial_Coordinates.csv")
coordenadas=coordenadas.set_index("Postal Code")
coordenadas

Latitude  Longitude
Postal Code                      
M1B          43.806686 -79.194353
M1C          43.784535 -79.160497
M1E          43.763573 -79.188711
M1G          43.770992 -79.216917
M1H          43.773136 -79.239476
M1J          43.744734 -79.239476
M1K          43.727929 -79.262029
M1L          43.711112 -79.284577
M1M          43.716316 -79.239476
M1N          43.692657 -79.264848
M1P          43.757410 -79.273304
M1R          43.750071 -79.295849
M1S          43.794200 -79.262029
M1T          43.781638 -79.304302
M1V          43.815252 -79.284577
M1W          43.799525 -79.318389
M1X          43.836125 -79.205636
M2H          43.803762 -79.363452
M2J          43.778517 -79.346556
M2K          43.786947 -79.385975
M2L          43.757490 -79.374714
M2M          43.789053 -79.408493
M2N          43.770120 -79.408493
M2P          43.752758 -79.400049
M2R          43.782736 -79.442259
M3A          43.753259 -79.329656
M3B          43.745906 -79.352188
M3C          43.725900 -79.340923
M3H          43.754328 -79.442259
M3J          43.767980 -79.487262
M3K          43.737473 -79.464763
M3L          43.739015 -79.506944
M3M          43.728496 -79.495697
M3N          43.761631 -79.520999
M4A          43.725882 -79.315572
M4B          43.706397 -79.309937
M4C          43.695344 -79.318389
M4E          43.676357 -79.293031
M4G          43.709060 -79.363452
M4H          43.705369 -79.349372
M4J          43.685347 -79.338106
M4K          43.679557 -79.352188
M4L          43.668999 -79.315572
M4M          43.659526 -79.340923
M4N          43.728020 -79.388790
M4P          43.712751 -79.390197
M4R          43.715383 -79.405678
M4S          43.704324 -79.388790
M4T          43.689574 -79.383160
M4V          43.686412 -79.400049
M4W          43.679563 -79.377529
M4X          43.667967 -79.367675
M4Y          43.665860 -79.383160
M5A          43.654260 -79.360636
M5B          43.657162 -79.378937
M5C          43.651494 -79.375418
M5E          43.644771 -79.373306
M5G          43.657952 -79.387383
M5H          43.650571 -79.384568
M5J          43.640816 -79.381752
M5K          43.647177 -79.381576
M5L          43.648198 -79.379817
M5M          43.733283 -79.419750
M5N          43.711695 -79.416936
M5P          43.696948 -79.411307
M5R          43.672710 -79.405678
M5S          43.662696 -79.400049
M5T          43.653206 -79.400049
M5V          43.628947 -79.394420
M5W          43.646435 -79.374846
M5X          43.648429 -79.382280
M6A          43.718518 -79.464763
M6B          43.709577 -79.445073
M6C          43.693781 -79.428191
M6E          43.689026 -79.453512
M6G          43.669542 -79.422564
M6H          43.669005 -79.442259
M6J          43.647927 -79.419750
M6K          43.636847 -79.428191
M6L          43.713756 -79.490074
M6M          43.691116 -79.476013
M6N          43.673185 -79.487262
M6P          43.661608 -79.464763
M6R          43.648960 -79.456325
M6S          43.651571 -79.484450
M7A          43.662301 -79.389494
M7R          43.636966 -79.615819
M7Y          43.662744 -79.321558
M8V          43.605647 -79.501321
M8W          43.602414 -79.543484
M8X          43.653654 -79.506944
M8Y          43.636258 -79.498509
M8Z          43.628841 -79.520999
M9A          43.667856 -79.532242
M9B          43.650943 -79.554724
M9C          43.643515 -79.577201
M9L          43.756303 -79.565963
M9M          43.724766 -79.532242
M9N          43.706876 -79.518188
M9P          43.696319 -79.532242
M9R          43.688905 -79.554724
M9V          43.739416 -79.588437
M9W          43.706748 -79.594054

In [164]:
#Agrega las dos columnas de latitud y longitud
df2=df.assign(Latitude = coordenadas["Latitude"])
df3=df2.assign(Longitude = coordenadas["Longitude"])
df3

Borough  \
PostalCode                     
M3A               North York   
M4A               North York   
M5A         Downtown Toronto   
M6A               North York   
M7A             Queen's Park   
M9A                Etobicoke   
M1B              Scarborough   
M3B               North York   
M4B                East York   
M5B         Downtown Toronto   
M6B               North York   
M9B                Etobicoke   
M1C              Scarborough   
M3C               North York   
M4C                East York   
M5C         Downtown Toronto   
M6C                     York   
M9C                Etobicoke   
M1E              Scarborough   
M4E             East Toronto   
M5E         Downtown Toronto   
M6E                     York   
M1G              Scarborough   
M4G                East York   
M5G         Downtown Toronto   
M6G         Downtown Toronto   
M1H              Scarborough   
M2H               North York   
M3H               North York   
M4H                East York   
M5H         Downtown Toronto   
M6H             West Toronto   
M1J              Scarborough   
M2J               North York   
M3J               North York   
M4J                East York   
M5J         Downtown Toronto   
M6J             West Toronto   
M1K              Scarborough   
M2K               North York   
M3K               North York   
M4K             East Toronto   
M5K         Downtown Toronto   
M6K             West Toronto   
M1L              Scarborough   
M2L               North York   
M3L               North York   
M4L             East Toronto   
M5L         Downtown Toronto   
M6L               North York   
M9L               North York   
M1M              Scarborough   
M2M               North York   
M3M               North York   
M4M             East Toronto   
M5M               North York   
M6M                     York   
M9M               North York   
M1N              Scarborough   
M2N               North York   
M3N               North York   
M4N          Central Toronto   
M5N          Central Toronto   
M6N                     York   
M9N                     York   
M1P              Scarborough   
M2P               North York   
M4P          Central Toronto   
M5P          Central Toronto   
M6P             West Toronto   
M9P                Etobicoke   
M1R              Scarborough   
M2R               North York   
M4R          Central Toronto   
M5R          Central Toronto   
M6R             West Toronto   
M7R              Mississauga   
M9R                Etobicoke   
M1S              Scarborough   
M4S          Central Toronto   
M5S         Downtown Toronto   
M6S             West Toronto   
M1T              Scarborough   
M4T          Central Toronto   
M5T         Downtown Toronto   
M1V              Scarborough   
M4V          Central Toronto   
M5V         Downtown Toronto   
M8V                Etobicoke   
M9V                Etobicoke   
M1W              Scarborough   
M4W         Downtown Toronto   
M5W         Downtown Toronto   
M8W                Etobicoke   
M9W                Etobicoke   
M1X              Scarborough   
M4X         Downtown Toronto   
M5X         Downtown Toronto   
M8X                Etobicoke   
M4Y         Downtown Toronto   
M7Y             East Toronto   
M8Y                Etobicoke   
M8Z                Etobicoke   

                                                 Neighborhood   Latitude  \
PostalCode                                                                 
M3A                                                 Parkwoods  43.753259   
M4A                                          Victoria Village  43.725882   
M5A                                 Regent Park, Harbourfront  43.654260   
M6A                          Lawrence Manor, Lawrence Heights  43.718518   
M7A                             Ontario Provincial Government  43.662301   
M9A                                          Islington Avenue  43.667856   
M1B                                            Malve

In [165]:
#Análisis de agrupación y segmentación solo para TORONTO

df3 = df3.drop(df3[df3['Borough']=="East York"].index)
df3 = df3.drop(df3[df3['Borough']=="Etobicoke"].index)
df3 = df3.drop(df3[df3['Borough']=="Mississauga"].index)
df3 = df3.drop(df3[df3['Borough']=="North York"].index)
df3 = df3.drop(df3[df3['Borough']=="Queen's Park"].index)
df3 = df3.drop(df3[df3['Borough']=="Scarborough"].index)
df3 = df3.drop(df3[df3['Borough']=="York"].index)
df3

Borough  \
PostalCode                     
M5A         Downtown Toronto   
M5B         Downtown Toronto   
M5C         Downtown Toronto   
M4E             East Toronto   
M5E         Downtown Toronto   
M5G         Downtown Toronto   
M6G         Downtown Toronto   
M5H         Downtown Toronto   
M6H             West Toronto   
M5J         Downtown Toronto   
M6J             West Toronto   
M4K             East Toronto   
M5K         Downtown Toronto   
M6K             West Toronto   
M4L             East Toronto   
M5L         Downtown Toronto   
M4M             East Toronto   
M4N          Central Toronto   
M5N          Central Toronto   
M4P          Central Toronto   
M5P          Central Toronto   
M6P             West Toronto   
M4R          Central Toronto   
M5R          Central Toronto   
M6R             West Toronto   
M4S          Central Toronto   
M5S         Downtown Toronto   
M6S             West Toronto   
M4T          Central Toronto   
M5T         Downtown Toronto   
M4V          Central Toronto   
M5V         Downtown Toronto   
M4W         Downtown Toronto   
M5W         Downtown Toronto   
M4X         Downtown Toronto   
M5X         Downtown Toronto   
M4Y         Downtown Toronto   
M7Y             East Toronto   

                                                 Neighborhood   Latitude  \
PostalCode                                                                 
M5A                                 Regent Park, Harbourfront  43.654260   
M5B                                  Garden District, Ryerson  43.657162   
M5C                                            St. James Town  43.651494   
M4E                                               The Beaches  43.676357   
M5E                                               Berczy Park  43.644771   
M5G                                        Central Bay Street  43.657952   
M6G                                                  Christie  43.669542   
M5H                                  Richmond, Adelaide, King  43.650571   
M6H                              Dufferin, Dovercourt Village  43.669005   
M5J         Harbourfront East, Union Station, Toronto Islands  43.640816   
M6J                                  Little Portugal, Trinity  43.647927   
M4K                              The Danforth West, Riverdale  43.679557   
M5K                  Toronto Dominion Centre, Design Exchange  43.647177   
M6K              Brockton, Parkdale Village, Exhibition Place  43.636847   
M4L                            India Bazaar, The Beaches West  43.668999   
M5L                            Commerce Court, Victoria Hotel  43.648198   
M4M                                           Studio District  43.659526   
M4N                                             Lawrence Park  43.728020   
M5N                                                  Roselawn  43.711695   
M4P                                          Davisville North  43.712751   
M5P                                  Forest Hill North & West  43.696948   
M6P                             High Park, The Junction South  43.661608   
M4R                                        North Toronto West  43.715383   
M5R                       The Annex, North Midtown, Yorkville  43.672710   
M6R                                    Parkdale, Roncesvalles  43.648960   
M4S                                                Davisville  43.704324   
M5S                            University of Toronto, Harbord  43.662696   
M6S                                        Runnymede, Swansea  43.651571   
M4T                               Moore Park, Summerhill East  43.689574   
M5T                 Kensington Market, Chinatown, Grange Park  43.653206   
M4V         Summerhill West, Rathnelly, South Hill, Forest...  43.686412   
M5V         CN Tower, King and Spadina, Railway Lands, Har...  43.628947   
M4W                                                  Rosedale  43.679563   
M5W                                            Stn A PO Boxes  43.646435   
M4X 

In [166]:
#Crear mapa inicial (con radio 20)
latitude=43.7166
longitude=-79.3407
map_toronto = folium.Map(location=[latitude, longitude], zoom_start=10)

# añadir marcadores al mapa
for lat, lng, borough, neighborhood in zip(df3['Latitude'], df3['Longitude'], df3['Borough'], df3['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=20,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
#         fill_opacity=0.7,
        parse_html=False).add_to(map_toronto)  
    
map_toronto

In [167]:
#Para cada zona por Código Postal se le saca los locales que tienen y se ponen en un solo dataframe
df=pd.DataFrame()
for i in range(len(df3)):
    url="https://api.foursquare.com/v3/places/nearby?ll={}%2C{}&limit=50".format(df3["Latitude"][i],df3["Longitude"][i])
    headers = {"Accept": "application/json","Authorization": "fsq3H9/faPTYfJlDZmuigCc0PYIPtX8KGAw0HUgAnlSSvkE="}
    response = requests.request("GET", url, headers=headers).json()
    results=json_normalize(response["results"])
    df=df.append(results)

#Muestra todos los locales contemplados
df

<ipython-input-167-bc598faa87e8>:7: FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead
  results=json_normalize(response["results"])


fsq_id  \
0   61845b587f081a47081cf050   
1   5e5d749285a0610007e60fe8   
2   4dc9d4d9d16495ca5add0803   
3   5e3618557bde930007d18b8d   
4   54ea41ad498e9a11e9e13308   
5   4bc70f5d14d7952126a066e9   
6   53b8466a498e83df908c3f21   
7   5aad9b86fdb9a7176b2d50ac   
8   574c229e498ebb5c6b257902   
9   5cd60624b9b37b002c47e8e3   
10  576864be498e42995f045b4e   
11  4ae5b91ff964a520a6a121e3   
12  54248f4e498e455132a5cee7   
13  4e8b7fa1cc2112f67517660a   
14  4dd27b4d227159fef24ba1c2   
15  4cc5a24d82388cfa1ec27635   
16  4bfd8d52f61dc9b6d8309fde   
17  4beb288d62c0c928dcc8e1d4   
18  50760559e4b0e8c7babe2497   
19  4beb1543415e20a10cdde5bb   
20  5151c3fde4b02da132c9553e   
21  4e54574bb61c93816c084ddb   
22  593c465b67af3a7da066e73d   
23  4c12aaf7a9c220a14d6a549d   
24  4ca5fcd576d3a09316dcfc6a   
25  4e4fe1352271a1bdc3e4528a   
26  58d423c99398ab4da84d0a7a   
27  5df44bb28a06ab0008f849b7   
28  4d94bab61646a35d03823da3   
29  5252ab1311d257ce2b04c870   
30  5095afb6e4b0abc85696c8bf   
31  4bf5a3025e800f47cedfe5d4   
32  4b1951c1f964a5202edb23e3   
33  4b745564f964a520dbd52de3   
34  4cfd3c862d80a14396c255d8   
35  4d2003878629224b7fb20f87   
0   4bd884d2f645c9b60c23a8e0   
1   4ba0c096f964a5203c7b37e3   
2   4fb13c20e4b011e6f93513c0   
3   59aed342d3cce86105e820cb   
4   4c0e64fe98102d7fca8be306   
5   4d9344ee9213b1f7332ac446   
6   502ad662e4b0cc2719059805   
7   57523e81498ea717003c7656   
8   55a9bbf9498e00ffd7f4c71f   
9   4eb2bd946da1df5f01ea25c5   
10  4aefac72f964a520ded921e3   
11  4b4ce994f964a520f3c326e3   
12  4d21f9a05c4ca1cdd1f9ad3d   
13  5cb912203149b9002c58ee97   
14  5d12b07d348eba0023182529   
15  4d1cdda5d2a3a090cbd26772   
16  4b82c2d4f964a52010e330e3   
17  4bfdce774cf820a1ff14edf4   
18  4bacbe2af964a5209a083be3   
19  4ba683f2f964a520fa5939e3   
20  4ae9e297f964a5204db721e3   
21  4e5423a2c65b9614d8e397e8   
22  50be660be4b0b67e339a983a   
23  4af87506f964a5206c0d22e3   
24  4b9800b5f964a520602535e3   
25  5f5d95a954e9ca2cdb9d04c7   
26  4c115d6ef6ba9c749eb91874   
27  61cf7bf85d7a433fdb81be16   
28  4c1bd48fb4e62d7fb00cda93   
29  4ae1b49ff964a520d78621e3   
30  4b098e31f964a520551923e3   
31  4cd2e74d3e0c8cfa87971a12   
32  4b86f131f964a52034a731e3   
33  50c16928e4b0533e0b020f0c   
34  4e01172b88776240d3f3f53d   
35  553f91b0498e44acdf31f171   
0   574ad72238fa943556d93b8e   
1   57963897498e6873394a559d   
2   4b2dd73cf964a520afdb24e3   
3   4be5b5fd910020a1a75cd314   
4   4b49183ff964a520a46526e3   
5   51b1f2c8498e1ddbd63b1b44   
6   519e7f64498ecf56b998428d   
7   4e93d58161afe52cf37528f4   
8   4ad4c05cf964a520e0f520e3   
9   4ad4c05cf964a520fbf520e3   
10  5d644f14b931cc00082b493b   
11  56b2cbf6498e44fd8f81c030   
12  4dc718dbae608779d164782a   
13  4d81105cf724a093424c1af7   
14  4b4e764af964a5209cee26e3   
15  4bd31815462cb713487edd07   
16  521a7f3411d245d46ae6f9c6   
17  4b69b45df964a520dfae2be3   
18  4b999927f964a5207c8635e3   
19  512f523fe4b0aa46ce2e57a4   
20  57a24865498e312f88271fb3   
21  50880c58498ea7b5aa812033   
22  4cdf697b94c3b60c88e96bea   
23  4edea5de4901ab1d4e6cd69d   
24  5c6474c3033693002ccba1bb   
25  4c51c987250dd13a576fd07d   
26  4e657daee4cdf1e2c09a9ec6   
27  4c328a3a7cc0c9b6dc88f09a   
28  4b44d90bf964a5200afe25e3   
29  4b63ebbdf964a5202d972ae3   
30  593f4ee0da70804c4b643f89   
31  4e15c91318a8addae8cce518   
32  5706e7e5498e19cf00254853   
33  4b44d003f964a520f3fc25e3   
34  4b8d6b7df964a52098fa32e3   
35  4c586576b7a31b8ddd6e52da   
36  56db8107cd107bf5eef15dd4   
37  4d7d542fe04d6ea8db7e0bd6   
38  4ada863ef964a5203c2321e3   
39  4ae6e9bff964a5207ea721e3   
40  4d63ee2aa45b5481ac30072d   
41  4ded09d0fa766152f057d48f   
0   4bd461bc77b29c74a07d9282   
1   4dbc8fe96a23e294ba3237bd   
2   5ea88bfaa7a46800077a492c   
3   4b8daea1f964a520480833e3   
4   4dbdfa5effcbcd485670ef68   
5   4c153eecb7b9c928afa5ac37   
6   51db85fb498e6e284e9b7130   
7   4c0012a4360a9c74f3e6d8a0   
8   4c0e34d27189c9289e0cd8b6   
9   4ba3fda9f964a5201a7538e3   
10  4d56b306fb65236a77

In [168]:
#Elimina las columnas no interesadas y resetea el índice
df2=df[['categories',"geocodes.main.latitude","geocodes.main.longitude"]]
df2.reset_index(drop=True, inplace=True) #La opción inplace=True es para que en lugar de retornar un dataframe nuevo, haga los cambios sobre el propio dataframe, y la opción drop=True es para que no cree la columna nueva llamada "index" con los valores del antiguo índice.
df2

categories  \
0     [{'id': 18027, 'name': 'Pilates Studio', 'icon...   
1     [{'id': 17068, 'name': 'Gourmet Store', 'icon'...   
2     [{'id': 11010, 'name': 'Automotive Repair Shop...   
3     [{'id': 13236, 'name': 'Italian Restaurant', '...   
4     [{'id': 13002, 'name': 'Bakery', 'icon': {'pre...   
5     [{'id': 11001, 'name': 'Advertising Agency', '...   
6     [{'id': 13034, 'name': 'Café', 'icon': {'prefi...   
7     [{'id': 13009, 'name': 'Cocktail Bar', 'icon':...   
8     [{'id': 11031, 'name': 'Distribution Center', ...   
9     [{'id': 13302, 'name': 'Mediterranean Restaura...   
10    [{'id': 10047, 'name': 'Public Art', 'icon': {...   
11    [{'id': 13049, 'name': 'Diner', 'icon': {'pref...   
12    [{'id': 17006, 'name': 'Car Dealership', 'icon...   
13    [{'id': 18025, 'name': 'Dance Studio', 'icon':...   
14    [{'id': 17006, 'name': 'Car Dealership', 'icon...   
15    [{'id': 12066, 'name': 'City Hall', 'icon': {'...   
16    [{'id': 17056, 'name': 'Flower Store', 'icon':...   
17    [{'id': 17082, 'name': 'Furniture and Home Sto...   
18    [{'id': 11073, 'name': 'Spa', 'icon': {'prefix...   
19    [{'id': 11007, 'name': 'Auditorium', 'icon': {...   
20    [{'id': 16033, 'name': 'Dog Park', 'icon': {'p...   
21    [{'id': 16033, 'name': 'Dog Park', 'icon': {'p...   
22    [{'id': 17006, 'name': 'Car Dealership', 'icon...   
23    [{'id': 15054, 'name': 'Veterinarian', 'icon':...   
24    [{'id': 11094, 'name': 'Painter', 'icon': {'pr...   
25    [{'id': 17082, 'name': 'Furniture and Home Sto...   
26    [{'id': 19048, 'name': 'Rental Car Location', ...   
27    [{'id': 17006, 'name': 'Car Dealership', 'icon...   
28    [{'id': 18021, 'name': 'Gym and Studio', 'icon...   
29    [{'id': 11001, 'name': 'Advertising Agency', '...   
30    [{'id': 12094, 'name': 'Residential Building',...   
31    [{'id': 11010, 'name': 'Automotive Repair Shop...   
32    [{'id': 13034, 'name': 'Café', 'icon': {'prefi...   
33    [{'id': 17000, 'name': 'Retail', 'icon': {'pre...   
34                                                   []   
35                                                   []   
36    [{'id': 13276, 'name': 'Sushi Restaurant', 'ic...   
37    [{'id': 11030, 'name': 'Design Studio', 'icon'...   
38    [{'id': 13034, 'name': 'Café', 'icon': {'prefi...   
39    [{'id': 13144, 'name': 'Falafel Restaurant', '...   
40    [{'id': 12023, 'name': 'College Communications...   
41    [{'id': 12017, 'name': 'College Auditorium', '...   
42    [{'id': 10004, 'name': 'Art Gallery', 'icon': ...   
43    [{'id': 15007, 'name': 'Dentist', 'icon': {'pr...   
44    [{'id': 13305, 'name': 'Burrito Restaurant', '...   
45    [{'id': 12016, 'name': 'College Arts Building'...   
46    [{'id': 13006, 'name': 'Beer Bar', 'icon': {'p...   
47    [{'id': 12014, 'name': 'College Academic Build...   
48    [{'id': 16030, 'name': 'Other Great Outdoors',...   
49    [{'id': 13199, 'name': 'Indian Restaurant', 'i...   
50    [{'id': 12013, 'name': 'College and University...   
51    [{'id': 16023, 'name': 'Lake', 'icon': {'prefi...   
52    [{'id': 12020, 'name': 'College Bookstore', 'i...   
53    [{'id': 19020, 'name': 'Parking', 'icon': {'pr...   
54    [{'id': 11130, 'name': 'Office Building', 'ico...   
55    [{'id': 13065, 'name': 'Restaurant', 'icon': {...   
56    [{'id': 12016, 'name': 'College Arts Building'...   
57    [{'id': 16026, 'name': 'Monument', 'icon': {'p...   
58    [{'id': 12015, 'name': 'College Administrative...   
59    [{'id': 12014, 'name': 'College Academic Build...   
60    [{'id': 12035, 'name': 'College Residence Hall...   
61    [{'id': 13057, 'name': 'Gastropub', 'icon': {'...   
62    [{'id': 12047, 'name': 'Student Center', 'icon...   
63    [{'id': 13072, 'name': 'Asian Restaurant', 'ic...   
64    [{'id': 17112, 'name': 'Print Store', 'icon': ...   
65    [{'id': 12086, 'name': 'Non-Profit Organizatio...   
66                                                   []   
67    [{'id': 11057, 'name': 'Cat

In [169]:
#Elimina los vacíos de categories
lista_eliminar=[]
for i in range(len(df2)):
    if len(df2["categories"][i])==0:
        lista_eliminar.append(i)
df2=df2.drop(lista_eliminar)
df2.reset_index(drop=True, inplace=True) #La opción inplace=True es para que en lugar de retornar un dataframe nuevo, haga los cambios sobre el propio dataframe, y la opción drop=True es para que no cree la columna nueva llamada "index" con los valores del antiguo índice.
df2

categories  \
0     [{'id': 18027, 'name': 'Pilates Studio', 'icon...   
1     [{'id': 17068, 'name': 'Gourmet Store', 'icon'...   
2     [{'id': 11010, 'name': 'Automotive Repair Shop...   
3     [{'id': 13236, 'name': 'Italian Restaurant', '...   
4     [{'id': 13002, 'name': 'Bakery', 'icon': {'pre...   
5     [{'id': 11001, 'name': 'Advertising Agency', '...   
6     [{'id': 13034, 'name': 'Café', 'icon': {'prefi...   
7     [{'id': 13009, 'name': 'Cocktail Bar', 'icon':...   
8     [{'id': 11031, 'name': 'Distribution Center', ...   
9     [{'id': 13302, 'name': 'Mediterranean Restaura...   
10    [{'id': 10047, 'name': 'Public Art', 'icon': {...   
11    [{'id': 13049, 'name': 'Diner', 'icon': {'pref...   
12    [{'id': 17006, 'name': 'Car Dealership', 'icon...   
13    [{'id': 18025, 'name': 'Dance Studio', 'icon':...   
14    [{'id': 17006, 'name': 'Car Dealership', 'icon...   
15    [{'id': 12066, 'name': 'City Hall', 'icon': {'...   
16    [{'id': 17056, 'name': 'Flower Store', 'icon':...   
17    [{'id': 17082, 'name': 'Furniture and Home Sto...   
18    [{'id': 11073, 'name': 'Spa', 'icon': {'prefix...   
19    [{'id': 11007, 'name': 'Auditorium', 'icon': {...   
20    [{'id': 16033, 'name': 'Dog Park', 'icon': {'p...   
21    [{'id': 16033, 'name': 'Dog Park', 'icon': {'p...   
22    [{'id': 17006, 'name': 'Car Dealership', 'icon...   
23    [{'id': 15054, 'name': 'Veterinarian', 'icon':...   
24    [{'id': 11094, 'name': 'Painter', 'icon': {'pr...   
25    [{'id': 17082, 'name': 'Furniture and Home Sto...   
26    [{'id': 19048, 'name': 'Rental Car Location', ...   
27    [{'id': 17006, 'name': 'Car Dealership', 'icon...   
28    [{'id': 18021, 'name': 'Gym and Studio', 'icon...   
29    [{'id': 11001, 'name': 'Advertising Agency', '...   
30    [{'id': 12094, 'name': 'Residential Building',...   
31    [{'id': 11010, 'name': 'Automotive Repair Shop...   
32    [{'id': 13034, 'name': 'Café', 'icon': {'prefi...   
33    [{'id': 17000, 'name': 'Retail', 'icon': {'pre...   
34    [{'id': 13276, 'name': 'Sushi Restaurant', 'ic...   
35    [{'id': 11030, 'name': 'Design Studio', 'icon'...   
36    [{'id': 13034, 'name': 'Café', 'icon': {'prefi...   
37    [{'id': 13144, 'name': 'Falafel Restaurant', '...   
38    [{'id': 12023, 'name': 'College Communications...   
39    [{'id': 12017, 'name': 'College Auditorium', '...   
40    [{'id': 10004, 'name': 'Art Gallery', 'icon': ...   
41    [{'id': 15007, 'name': 'Dentist', 'icon': {'pr...   
42    [{'id': 13305, 'name': 'Burrito Restaurant', '...   
43    [{'id': 12016, 'name': 'College Arts Building'...   
44    [{'id': 13006, 'name': 'Beer Bar', 'icon': {'p...   
45    [{'id': 12014, 'name': 'College Academic Build...   
46    [{'id': 16030, 'name': 'Other Great Outdoors',...   
47    [{'id': 13199, 'name': 'Indian Restaurant', 'i...   
48    [{'id': 12013, 'name': 'College and University...   
49    [{'id': 16023, 'name': 'Lake', 'icon': {'prefi...   
50    [{'id': 12020, 'name': 'College Bookstore', 'i...   
51    [{'id': 19020, 'name': 'Parking', 'icon': {'pr...   
52    [{'id': 11130, 'name': 'Office Building', 'ico...   
53    [{'id': 13065, 'name': 'Restaurant', 'icon': {...   
54    [{'id': 12016, 'name': 'College Arts Building'...   
55    [{'id': 16026, 'name': 'Monument', 'icon': {'p...   
56    [{'id': 12015, 'name': 'College Administrative...   
57    [{'id': 12014, 'name': 'College Academic Build...   
58    [{'id': 12035, 'name': 'College Residence Hall...   
59    [{'id': 13057, 'name': 'Gastropub', 'icon': {'...   
60    [{'id': 12047, 'name': 'Student Center', 'icon...   
61    [{'id': 13072, 'name': 'Asian Restaurant', 'ic...   
62    [{'id': 17112, 'name': 'Print Store', 'icon': ...   
63    [{'id': 12086, 'name': 'Non-Profit Organizatio...   
64    [{'id': 11057, 'name': 'Caterer', 'icon': {'pr...   
65    [{'id': 12016, 'name': 'College Arts Building'...   
66    [{'id': 12015, 'name': 'College Administrative...   
67    [{'id': 17065, 'name': 'Far

In [170]:
#Extrae los tipos de locales
bandera=0
lista=[]
for i in range(len(df2)):
    pivot=df2["categories"][bandera]
    pivot2=pivot[0]["name"]
    lista.append(pivot2)
    bandera=bandera+1
lista

['Pilates Studio',
 'Gourmet Store',
 'Automotive Repair Shop',
 'Italian Restaurant',
 'Bakery',
 'Advertising Agency',
 'Café',
 'Cocktail Bar',
 'Distribution Center',
 'Mediterranean Restaurant',
 'Public Art',
 'Diner',
 'Car Dealership',
 'Dance Studio',
 'Car Dealership',
 'City Hall',
 'Flower Store',
 'Furniture and Home Store',
 'Spa',
 'Auditorium',
 'Dog Park',
 'Dog Park',
 'Car Dealership',
 'Veterinarian',
 'Painter',
 'Furniture and Home Store',
 'Rental Car Location',
 'Car Dealership',
 'Gym and Studio',
 'Advertising Agency',
 'Residential Building',
 'Automotive Repair Shop',
 'Café',
 'Retail',
 'Sushi Restaurant',
 'Design Studio',
 'Café',
 'Falafel Restaurant',
 'College Communications Building',
 'College Auditorium',
 'Art Gallery',
 'Dentist',
 'Burrito Restaurant',
 'College Arts Building',
 'Beer Bar',
 'College Academic Building',
 'Other Great Outdoors',
 'Indian Restaurant',
 'College and University',
 'Lake',
 'College Bookstore',
 'Parking',
 'Office B

In [171]:
#Los pone en la columna (se resuelve el primer punto de metodología)
df2["categories"]=lista
df2

categories  geocodes.main.latitude  \
0                              Pilates Studio               43.654054   
1                               Gourmet Store               43.653903   
2                      Automotive Repair Shop               43.654155   
3                          Italian Restaurant               43.654555   
4                                      Bakery               43.653473   
5                          Advertising Agency               43.654495   
6                                        Café               43.653597   
7                                Cocktail Bar               43.654036   
8                         Distribution Center               43.653056   
9                    Mediterranean Restaurant               43.653532   
10                                 Public Art               43.655701   
11                                      Diner               43.653848   
12                             Car Dealership               43.653230   
13                               Dance Studio               43.653359   
14                             Car Dealership               43.652791   
15                                  City Hall               43.654610   
16                               Flower Store               43.653473   
17                   Furniture and Home Store               43.652986   
18                                        Spa               43.654607   
19                                 Auditorium               43.652906   
20                                   Dog Park               43.654635   
21                                   Dog Park               43.654452   
22                             Car Dealership               43.653711   
23                               Veterinarian               43.655249   
24                                    Painter               43.656192   
25                   Furniture and Home Store               43.653393   
26                        Rental Car Location               43.656218   
27                             Car Dealership               43.653650   
28                             Gym and Studio               43.655721   
29                         Advertising Agency               43.653198   
30                       Residential Building               43.652385   
31                     Automotive Repair Shop               43.655523   
32                                       Café               43.653906   
33                                     Retail               43.653222   
34                           Sushi Restaurant               43.648782   
35                              Design Studio               43.657131   
36                                       Café               43.657532   
37                         Falafel Restaurant               43.657128   
38            College Communications Building               43.657617   
39                         College Auditorium               43.657558   
40                                Art Gallery               43.657564   
41                                    Dentist               43.657121   
42                         Burrito Restaurant               43.656331   
43                      College Arts Building               43.657473   
44                                   Beer Bar               43.656324   
45                  College Academic Building               43.656597   
46                       Other Great Outdoors               43.656895   
47                          Indian Restaurant               43.656390   
48                     College and University               43.656650   
49                                       Lake               43.657555   
50                          College Bookstore               43.657608   
51                                    Parking               43.656831   
52                            Office Building               43.656434   
53                                 Restaurant               43.656570   
54                  

In [172]:
# Con los unique sabemos que "Gym and Studio" y "College Gym" suplen la oferta de un gimnasio.
df2["categories"].unique()

array(['Pilates Studio', 'Gourmet Store', 'Automotive Repair Shop',
       'Italian Restaurant', 'Bakery', 'Advertising Agency', 'Café',
       'Cocktail Bar', 'Distribution Center', 'Mediterranean Restaurant',
       'Public Art', 'Diner', 'Car Dealership', 'Dance Studio',
       'City Hall', 'Flower Store', 'Furniture and Home Store', 'Spa',
       'Auditorium', 'Dog Park', 'Veterinarian', 'Painter',
       'Rental Car Location', 'Gym and Studio', 'Residential Building',
       'Retail', 'Sushi Restaurant', 'Design Studio',
       'Falafel Restaurant', 'College Communications Building',
       'College Auditorium', 'Art Gallery', 'Dentist',
       'Burrito Restaurant', 'College Arts Building', 'Beer Bar',
       'College Academic Building', 'Other Great Outdoors',
       'Indian Restaurant', 'College and University', 'Lake',
       'College Bookstore', 'Parking', 'Office Building', 'Restaurant',
       'Monument', 'College Administrative Building',
       'College Residence Hall', 'G

In [173]:
#Nos vamos a quedar solo con los que son gimnasios (públicos o de colegio) Resuelve el punto 2 de metodología
filtro = df2['categories']=="Gym and Studio"
df3_1=df2[filtro]

filtro = df2['categories']=="College Gym"
df3_2=df2[filtro]
df3=df3_1.append(df3_2)
df3

categories  geocodes.main.latitude  geocodes.main.longitude
28    Gym and Studio               43.655721               -79.361379
113   Gym and Studio               43.669362               -79.311090
250   Gym and Studio               43.650978               -79.384234
283   Gym and Studio               43.667946               -79.441888
337   Gym and Studio               43.640111               -79.381616
423   Gym and Studio               43.678018               -79.350372
436   Gym and Studio               43.677514               -79.351134
441   Gym and Studio               43.646752               -79.381364
451   Gym and Studio               43.647460               -79.380121
534   Gym and Studio               43.666895               -79.313069
550   Gym and Studio               43.648270               -79.379783
639   Gym and Studio               43.703804               -79.412964
734   Gym and Studio               43.717749               -79.400400
738   Gym and Studio               43.687296               -79.396710
872   Gym and Studio               43.662935               -79.401242
876   Gym and Studio               43.663148               -79.401786
898   Gym and Studio               43.663048               -79.400465
1243  Gym and Studio               43.665437               -79.384572
870      College Gym               43.663075               -79.400095

In [174]:
#Se crea un mapa con los puntos en cuestión (radio de 20 de influencia). Resuelve los puntos 3 y 4 de metodología.
latitude=43.7166
longitude=-79.3407
map_toronto = folium.Map(location=[latitude, longitude], zoom_start=10)

# añadir marcadores al mapa
for lat, lng, category in zip(df3['geocodes.main.latitude'], df3['geocodes.main.longitude'],df3["categories"]):
    label = '{}'.format(category)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=50,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        #fill_opacity=0.7,
        parse_html=False).add_to(map_toronto)  
    
map_toronto

## Conclusión final (solución al problema planteado)

Como se puede ver en el mapa hay una gran concentración de gimnasios en algunos puntos, pero hay zonas de Toronto en las que no está suplida la demanda de servicios y existe un potencial mercado por explotar.

De esta manera, se recomienda al emprendedor que coloque su gimnasio en alguno de estos dos cuadrantes:

1. Al sur de la Bloor Street West, entre Parkside Drive y Bathurst Street.
2. Al norte de Dupont Street entre Duffen Street y Barthurst Street.